# Parallel Hyperparameter Optimization with Optuna & MLflow

This notebook uses **true parallelization** by running different (dataset, algorithm) combinations in parallel.

**Strategy**: Instead of parallelizing trials within one study (limited by TPE coordination),
we parallelize the 15 independent optimization tasks (3 datasets × 5 algorithms).

This is **much faster** for small datasets!

## Configuration

In [ ]:
# Configuration
N_TRIALS = 2000  # Trials per (dataset, algorithm) combination
EXPERIMENT_NAME = "HPO_3_parallel"
ALGORITHMS = ['DTSCAN', 'DBSCAN', 'KMeans', 'Spectral', 'GMM', 'ASCDT', 'DTC']
N_JOBS = 6

## Imports

In [19]:
import sys
sys.path.insert(0, '../code')

import os
import numpy as np
import pandas as pd
import warnings
warnings.filterwarnings('ignore')

from multiprocessing import Pool, cpu_count
from functools import partial
import time

In [20]:
import optuna
import mlflow

In [21]:
from sklearn.cluster import DBSCAN, KMeans, SpectralClustering
from sklearn.mixture import GaussianMixture
from sklearn.preprocessing import StandardScaler
from sklearn.neighbors import NearestNeighbors

In [ ]:
from dtscan import DTSCAN, psr
from dtc import DTC
from ascdt import ASCDT
from cluster_sets import clusters_paper

import io
from contextlib import redirect_stdout

print("✓ All imports loaded")

✓ All imports loaded


## MLflow Setup

In [23]:
# Set MLflow tracking URI
mlflow.set_tracking_uri("file:../mlruns")
mlflow.set_experiment(EXPERIMENT_NAME)

print(f"✓ MLflow tracking: {mlflow.get_tracking_uri()}")
print(f"✓ Experiment: {EXPERIMENT_NAME}")

2025/11/21 20:02:52 INFO mlflow.tracking.fluent: Experiment with name 'HPO_2_parallel' does not exist. Creating a new experiment.


✓ MLflow tracking: file:../mlruns
✓ Experiment: HPO_2_parallel


## Load Datasets

In [24]:
# Load datasets
S1, S2, S3 = clusters_paper()

datasets = {
    'S1': (S1[['x', 'y']].values, S1['label'].values),
    'S2': (S2[['x', 'y']].values, S2['label'].values),
    'S3': (S3[['x', 'y']].values, S3['label'].values)
}

print("✓ Datasets loaded")

✓ Datasets loaded


In [25]:
# Display dataset information
for name, (X, labels) in datasets.items():
    n_clusters = len(np.unique(labels[labels != -1]))
    print(f"{name}: {X.shape[0]} points, {n_clusters} clusters")

S1: 788 points, 7 clusters
S2: 300 points, 3 clusters
S3: 373 points, 2 clusters


## Optimizer Functions

These are standalone functions that can run in separate processes.

In [ ]:
def objective_dtscan(trial, X, true_labels):
    """DTSCAN objective - optimizes for PSR score."""
    min_pts = trial.suggest_int('MinPts', 2, 20)
    area_threshold = trial.suggest_float('area_threshold', -40.0, 40.0)
    length_threshold = trial.suggest_float('length_threshold', -40.0, 40.0)
    
    try:
        dtscan = DTSCAN(MinPts=min_pts, area_threshold=area_threshold,
                       length_threshold=length_threshold)
        f = io.StringIO()
        with redirect_stdout(f):
            labels = dtscan.fit_predict(X)
        
        psr_score = psr(true_labels, labels)
        n_clusters = len(np.unique(labels[labels != -1]))
        
        trial.set_user_attr('n_clusters', n_clusters)
        return psr_score
    except:
        return 0.0

def objective_dbscan(trial, X_scaled, true_labels, eps_min, eps_max):
    """DBSCAN objective - optimizes for PSR score."""
    eps = trial.suggest_float('eps', eps_min, eps_max)
    min_samples = trial.suggest_int('min_samples', 3, 12)
    
    try:
        dbscan = DBSCAN(eps=eps, min_samples=min_samples)
        labels = dbscan.fit_predict(X_scaled)
        
        psr_score = psr(true_labels, labels)
        n_clusters = len(np.unique(labels[labels != -1]))
        
        trial.set_user_attr('n_clusters', n_clusters)
        return psr_score
    except:
        return 0.0

def objective_kmeans(trial, X_scaled, true_labels, expected_clusters):
    """K-means objective - optimizes for PSR score."""
    n_clusters = trial.suggest_int('n_clusters',
                                   max(2, expected_clusters - 2),
                                   expected_clusters + 5)
    n_init = trial.suggest_categorical('n_init', [5, 10, 20, 50])
    
    try:
        kmeans = KMeans(n_clusters=n_clusters, n_init=n_init, random_state=42)
        labels = kmeans.fit_predict(X_scaled)
        return psr(true_labels, labels)
    except:
        return 0.0

def objective_spectral(trial, X_scaled, true_labels, expected_clusters):
    """Spectral objective - optimizes for PSR score."""
    if len(X_scaled) > 1000:
        return 0.0
    
    n_clusters = trial.suggest_int('n_clusters',
                                   max(2, expected_clusters - 2),
                                   expected_clusters + 5)
    n_neighbors = trial.suggest_int('n_neighbors', 5, 30)
    
    try:
        spectral = SpectralClustering(n_clusters=n_clusters,
                                     n_neighbors=n_neighbors,
                                     affinity='nearest_neighbors',
                                     random_state=42)
        labels = spectral.fit_predict(X_scaled)
        return psr(true_labels, labels)
    except:
        return 0.0

def objective_gmm(trial, X_scaled, true_labels, expected_clusters):
    """GMM objective - optimizes for PSR score."""
    n_components = trial.suggest_int('n_components',
                                    max(2, expected_clusters - 2),
                                    expected_clusters + 5)
    covariance_type = trial.suggest_categorical('covariance_type',
                                                ['full', 'tied', 'diag', 'spherical'])
    n_init = trial.suggest_categorical('n_init', [1, 5, 10, 20])
    
    try:
        gmm = GaussianMixture(n_components=n_components,
                             covariance_type=covariance_type,
                             n_init=n_init,
                             random_state=42)
        labels = gmm.fit_predict(X_scaled)
        return psr(true_labels, labels)
    except:
        return 0.0

def objective_ascdt(trial, X, true_labels):
    """ASCDT objective - optimizes for PSR score."""
    min_cluster_size = trial.suggest_int('min_cluster_size', 2, 20)
    beta = trial.suggest_float('beta', 1.0, 1.5)
    
    try:
        ascdt = ASCDT(min_cluster_size=min_cluster_size, beta=beta)
        labels = ascdt.fit_predict(X)
        
        psr_score = psr(true_labels, labels)
        n_clusters = ascdt.n_clusters_
        
        trial.set_user_attr('n_clusters', n_clusters)
        return psr_score
    except Exception:
        return 0.0

def objective_dtc(trial, X, true_labels):
    """DTC objective - optimizes for PSR score."""
    minPts = trial.suggest_int('minPts', 2, 20)
    local_std = trial.suggest_float('local_std', 1.0, 5.0)
    
    try:
        df = pd.DataFrame(X, columns=['x', 'y'])
        
        tdbscan = DTC(data=df, minPts=minPts, local_std=local_std, kde=False)
        
        f = io.StringIO()
        with redirect_stdout(f):
            result_df = tdbscan.tri_dbscan()

        if result_df is None or 'est_clust' not in result_df.columns:
            return 0.0

        labels = result_df['est_clust'].values
        
        psr_score = psr(true_labels, labels)
        n_clusters = len(np.unique(labels[labels != 0]))
        
        trial.set_user_attr('n_clusters', n_clusters)
        return psr_score
    except Exception:
        return 0.0

print("✓ Objective functions defined")

✓ Objective functions defined


## Parallel Optimization Function

This function will be executed in parallel for each (dataset, algorithm) combination.

In [27]:
def optimize_single_task(task_params):
    """Optimize a single (dataset, algorithm) combination.
    
    This function runs in a separate process.
    """
    dataset_name, algorithm, X, true_labels, n_trials, experiment_name = task_params
    
    # Prepare data
    expected_clusters = len(np.unique(true_labels[true_labels != -1]))
    scaler = StandardScaler()
    X_scaled = scaler.fit_transform(X)
    
    # For DBSCAN, estimate eps range
    if algorithm == 'DBSCAN':
        nbrs = NearestNeighbors(n_neighbors=6).fit(X_scaled)
        distances, _ = nbrs.kneighbors(X_scaled)
        distances_sorted = np.sort(distances[:, 5])
        eps_min, eps_max = np.percentile(distances_sorted, [10, 90])
    
    # Setup study
    study_name = f"{dataset_name}_{algorithm}"
    
    # Use in-memory storage (each process has its own study)
    study = optuna.create_study(
        study_name=study_name,
        direction='maximize',
        sampler=optuna.samplers.TPESampler(seed=42)
    )
    
    # Select objective function
    if algorithm == 'DTSCAN':
        objective = lambda trial: objective_dtscan(trial, X, true_labels)
    elif algorithm == 'DBSCAN':
        objective = lambda trial: objective_dbscan(trial, X_scaled, true_labels, eps_min, eps_max)
    elif algorithm == 'KMeans':
        objective = lambda trial: objective_kmeans(trial, X_scaled, true_labels, expected_clusters)
    elif algorithm == 'Spectral':
        objective = lambda trial: objective_spectral(trial, X_scaled, true_labels, expected_clusters)
    elif algorithm == 'GMM':
        objective = lambda trial: objective_gmm(trial, X_scaled, true_labels, expected_clusters)
    elif algorithm == 'ASCDT':
        objective = lambda trial: objective_ascdt(trial, X, true_labels)
    elif algorithm == 'DTC':
        objective = lambda trial: objective_dtc(trial, X, true_labels)
    else:
        raise ValueError(f"Unknown algorithm: {algorithm}")
    
    # Optimize
    start_time = time.time()
    study.optimize(objective, n_trials=n_trials, show_progress_bar=False)
    duration = time.time() - start_time
    
    # Log to MLflow
    mlflow.set_tracking_uri("file:../mlruns")
    mlflow.set_experiment(experiment_name)
    
    with mlflow.start_run(run_name=study_name):
        mlflow.log_param("dataset", dataset_name)
        mlflow.log_param("algorithm", algorithm)
        mlflow.log_param("n_samples", len(X))
        mlflow.log_param("expected_clusters", expected_clusters)
        mlflow.log_param("n_trials", n_trials)
        mlflow.log_params(study.best_params)
        mlflow.log_metric("best_psr_score", study.best_value)
        mlflow.log_metric("optimization_time_seconds", duration)
        
        if 'n_clusters' in study.best_trial.user_attrs:
            mlflow.log_metric("best_n_clusters",
                            study.best_trial.user_attrs['n_clusters'])
    
    # Return results
    result = {
        'dataset': dataset_name,
        'algorithm': algorithm,
        'best_params': study.best_params,
        'best_psr': study.best_value,
        'expected_clusters': expected_clusters,
        'n_clusters': study.best_trial.user_attrs.get('n_clusters', None),
        'duration': duration
    }
    
    print(f"✓ {study_name}: PSR={study.best_value:.4f} ({duration:.1f}s)")
    
    return result

print("✓ Parallel optimization function defined")

✓ Parallel optimization function defined


## Run Parallel Optimization

This creates all tasks and runs them in parallel using multiprocessing.

In [28]:
# Check available CPU cores
n_cores = cpu_count()
n_jobs = n_cores if N_JOBS == -1 else N_JOBS

print(f"CPU cores available: {n_cores}")
print(f"Will use: {n_jobs} parallel processes")
print(f"Total tasks: {len(datasets)} datasets × {len(ALGORITHMS)} algorithms = {len(datasets) * len(ALGORITHMS)} tasks")

CPU cores available: 8
Will use: 8 parallel processes
Total tasks: 3 datasets × 5 algorithms = 15 tasks


In [29]:
# Create all tasks
tasks = []
for dataset_name, (X, labels) in datasets.items():
    for algorithm in ALGORITHMS:
        task = (dataset_name, algorithm, X, labels, N_TRIALS, EXPERIMENT_NAME)
        tasks.append(task)

print(f"✓ Created {len(tasks)} optimization tasks")

✓ Created 15 optimization tasks


In [30]:
# Run all tasks in parallel
print("\n" + "="*80)
print("STARTING PARALLEL OPTIMIZATION")
print("="*80)
print(f"Datasets: {list(datasets.keys())}")
print(f"Algorithms: {ALGORITHMS}")
print(f"Trials per task: {N_TRIALS}")
print(f"Parallel processes: {n_jobs}")
print("="*80 + "\n")

start_time = time.time()

if n_jobs == 1:
    # Sequential execution (for debugging)
    results = [optimize_single_task(task) for task in tasks]
else:
    # Parallel execution
    with Pool(processes=n_jobs) as pool:
        results = pool.map(optimize_single_task, tasks)

total_time = time.time() - start_time

print("\n" + "="*80)
print("PARALLEL OPTIMIZATION COMPLETE")
print("="*80)
print(f"Total time: {total_time:.1f} seconds ({total_time/60:.1f} minutes)")
print(f"Average time per task: {total_time/len(tasks):.1f} seconds")
print("="*80)


STARTING PARALLEL OPTIMIZATION
Datasets: ['S1', 'S2', 'S3']
Algorithms: ['DTSCAN', 'DBSCAN', 'KMeans', 'Spectral', 'GMM']
Trials per task: 2000
Parallel processes: 8



[I 2025-11-21 20:02:52,737] A new study created in memory with name: S1_DTSCAN
[I 2025-11-21 20:02:52,739] A new study created in memory with name: S1_KMeans
[I 2025-11-21 20:02:52,742] A new study created in memory with name: S1_DBSCAN
[I 2025-11-21 20:02:52,741] A new study created in memory with name: S1_GMM
[I 2025-11-21 20:02:52,742] A new study created in memory with name: S2_DTSCAN
[I 2025-11-21 20:02:52,744] A new study created in memory with name: S1_Spectral
[I 2025-11-21 20:02:52,750] Trial 0 finished with value: 0.07563025210084033 and parameters: {'eps': 0.11473042557039725, 'min_samples': 12}. Best is trial 0 with value: 0.07563025210084033.
[I 2025-11-21 20:02:52,754] Trial 1 finished with value: 0.8110238967381825 and parameters: {'eps': 0.13406283036564298, 'min_samples': 8}. Best is trial 1 with value: 0.8110238967381825.
[I 2025-11-21 20:02:52,751] A new study created in memory with name: S2_DBSCAN
[I 2025-11-21 20:02:52,748] A new study created in memory with name: 

✓ S2_DBSCAN: PSR=0.6830 (48.8s)

[I 2025-11-21 20:03:41,923] Trial 635 finished with value: 0.6866078591749505 and parameters: {'MinPts': 6, 'area_threshold': -19.064295932369077, 'length_threshold': -1.064617332945592}. Best is trial 494 with value: 0.9904115492350787.


[I 2025-11-21 20:03:41,930] A new study created in memory with name: S2_Spectral
[I 2025-11-21 20:03:41,937] Trial 1886 finished with value: 0.9648361908866112 and parameters: {'eps': 0.1232725170278983, 'min_samples': 6}. Best is trial 41 with value: 0.9801979840977965.
[I 2025-11-21 20:03:41,938] Trial 1153 finished with value: 0.0 and parameters: {'MinPts': 16, 'area_threshold': -35.06851633538041, 'length_threshold': 0.2080461921636161}. Best is trial 956 with value: 0.7345604717823925.
[I 2025-11-21 20:03:41,964] Trial 1154 finished with value: 0.0 and parameters: {'MinPts': 3, 'area_threshold': -38.50357588039628, 'length_threshold': 4.22696474798625}. Best is trial 956 with value: 0.7345604717823925.
[I 2025-11-21 20:03:41,959] Trial 1887 finished with value: 0.9739321469190116 and parameters: {'eps': 0.1402763098554561, 'min_samples': 7}. Best is trial 41 with value: 0.9801979840977965.
[I 2025-11-21 20:03:41,981] Trial 1888 finished with value: 0.9793576479633427 and parameter

...

✓ S3_GMM: PSR=0.7953 (1309.0s)


[I 2025-11-21 21:01:46,514] Trial 272 finished with value: 0.7560104309282243 and parameters: {'n_clusters': 7, 'n_init': 50}. Best is trial 19 with value: 0.7560104309282243.
[I 2025-11-21 21:01:46,727] Trial 1688 finished with value: 0.9929092174584547 and parameters: {'n_components': 7, 'covariance_type': 'spherical', 'n_init': 20}. Best is trial 7 with value: 0.9929092174584547.
[I 2025-11-21 21:01:46,946] Trial 273 finished with value: 0.7560104309282243 and parameters: {'n_clusters': 7, 'n_init': 20}. Best is trial 19 with value: 0.7560104309282243.
[I 2025-11-21 21:01:46,950] Trial 1689 finished with value: 0.9929092174584547 and parameters: {'n_components': 7, 'covariance_type': 'spherical', 'n_init': 5}. Best is trial 7 with value: 0.9929092174584547.
[I 2025-11-21 21:01:47,082] Trial 1690 finished with value: 0.9929092174584547 and parameters: {'n_components': 7, 'covariance_type': 'spherical', 'n_init': 5}. Best is trial 7 with value: 0.9929092174584547.
[I 2025-11-21 21:01:

✓ S1_GMM: PSR=0.9929 (3598.9s)


[I 2025-11-21 21:02:51,710] Trial 355 finished with value: 0.7560104309282243 and parameters: {'n_clusters': 7, 'n_init': 20}. Best is trial 19 with value: 0.7560104309282243.
[I 2025-11-21 21:02:51,986] Trial 356 finished with value: 0.7560104309282243 and parameters: {'n_clusters': 7, 'n_init': 50}. Best is trial 19 with value: 0.7560104309282243.
[I 2025-11-21 21:02:52,050] Trial 357 finished with value: 0.7560104309282243 and parameters: {'n_clusters': 7, 'n_init': 50}. Best is trial 19 with value: 0.7560104309282243.
[I 2025-11-21 21:02:52,075] Trial 358 finished with value: 0.7560104309282243 and parameters: {'n_clusters': 7, 'n_init': 10}. Best is trial 19 with value: 0.7560104309282243.
[I 2025-11-21 21:02:52,144] Trial 359 finished with value: 0.7560104309282243 and parameters: {'n_clusters': 7, 'n_init': 50}. Best is trial 19 with value: 0.7560104309282243.
[I 2025-11-21 21:02:52,207] Trial 360 finished with value: 0.7560104309282243 and parameters: {'n_clusters': 7, 'n_init'

✓ S1_KMeans: PSR=0.7560 (3677.0s)

PARALLEL OPTIMIZATION COMPLETE
Total time: 3677.2 seconds (61.3 minutes)
Average time per task: 245.1 seconds


## Organize Results

In [31]:
# Organize results by dataset and algorithm
all_results = {}
for result in results:
    dataset = result['dataset']
    algorithm = result['algorithm']
    
    if dataset not in all_results:
        all_results[dataset] = {}
    
    all_results[dataset][algorithm] = result

print("✓ Results organized by dataset and algorithm")

✓ Results organized by dataset and algorithm


## Results Summary

In [32]:
# Create results DataFrame
results_data = []
for dataset_name, algo_results in all_results.items():
    for algo_name, result in algo_results.items():
        row = {
            'Dataset': dataset_name,
            'Algorithm': algo_name,
            'PSR Score': result['best_psr'],
            'N Clusters': result.get('n_clusters', 'N/A'),
            'Expected': result['expected_clusters'],
            'Time (s)': f"{result['duration']:.1f}"
        }
        results_data.append(row)

results_df = pd.DataFrame(results_data)
results_df = results_df.sort_values(['Dataset', 'PSR Score'], ascending=[True, False])

print("\n" + "="*80)
print("RESULTS SUMMARY")
print("="*80)
print(results_df.to_string(index=False))


RESULTS SUMMARY
Dataset Algorithm  PSR Score  N Clusters  Expected Time (s)
     S1       GMM   0.992909         NaN         7   3598.9
     S1    DTSCAN   0.991775         7.0         7    201.6
     S1  Spectral   0.988531         NaN         7   3508.3
     S1    DBSCAN   0.980198         7.0         7     53.5
     S1    KMeans   0.756010         NaN         7   3677.0
     S2    DTSCAN   0.734560         6.0         3    105.9
     S2       GMM   0.727894         NaN         3   2364.3
     S2    DBSCAN   0.682973        14.0         3     48.8
     S2  Spectral   0.659432         NaN         3   2175.1
     S2    KMeans   0.598718         NaN         3   3528.9
     S3  Spectral   1.000000         NaN         2   2114.8
     S3    DTSCAN   0.993086         2.0         2    129.5
     S3    DBSCAN   0.850515         4.0         2     58.7
     S3       GMM   0.795318         NaN         2   1309.0
     S3    KMeans   0.750827         NaN         2   2869.0


In [33]:
# Find best algorithm per dataset
print("\n" + "="*80)
print("BEST ALGORITHM PER DATASET")
print("="*80)

for dataset in ['S1', 'S2', 'S3']:
    dataset_df = results_df[results_df['Dataset'] == dataset]
    if len(dataset_df) > 0:
        best = dataset_df.loc[dataset_df['PSR Score'].idxmax()]
        print(f"\n{dataset}: {best['Algorithm']} (PSR: {best['PSR Score']:.4f})")


BEST ALGORITHM PER DATASET

S1: GMM (PSR: 0.9929)

S2: DTSCAN (PSR: 0.7346)

S3: Spectral (PSR: 1.0000)


## Export Results

In [34]:
import json

# Format for JSON export
export_data = {}
for dataset_name, algo_results in all_results.items():
    export_data[dataset_name] = {}
    for algo_name, result in algo_results.items():
        export_data[dataset_name][algo_name] = {
            'best_params': result['best_params'],
            'psr_score': float(result['best_psr']),
            'n_clusters': int(result['n_clusters']) if result['n_clusters'] else None,
            'expected_clusters': int(result['expected_clusters']),
            'optimization_time_seconds': float(result['duration'])
        }

# Save to JSON
output_file = 'best_params_parallel.json'
with open(output_file, 'w') as f:
    json.dump(export_data, f, indent=2)

print(f"✓ Results exported to {output_file}")

✓ Results exported to best_params_parallel.json


## Next Steps

1. **View in MLflow UI**: `mlflow ui --backend-store-uri file:../mlruns`
2. **Load best parameters**: Use the `best_params_parallel.json` file
3. **Compare with sequential version**: Check time savings!

### Performance Notes

This parallel approach is faster because:
- **Independent tasks**: Each (dataset, algorithm) runs completely independently
- **No coordination overhead**: No shared TPE sampler state
- **Better CPU utilization**: For small datasets, trial computation is fast, so we benefit from parallelizing at the task level

Typical speedup: ~Linear with number of cores (e.g., 8 cores ≈ 8× faster)